In [4]:
import os
os.getcwd()


'c:\\Users\\Jeconchao\\Desktop\\Repos\\repo-simce'

In [9]:
from simce.proc_imgs import get_mask_naranjo, recorte_imagen, get_n_paginas, get_n_preguntas
import cv2

from simce.config import dir_estudiantes, dir_tabla_99
from simce.utils import crear_directorios
from pathlib import Path
import re
import numpy as np
import simce.proc_imgs as proc
import pandas as pd


# Creamos directorios
crear_directorios()

n_pages = 12
n_preguntas = 29
n_subpreg_tot = 165
revisar_pregunta = []

In [10]:
CASOS99_FINAL = pd.read_csv(dir_tabla_99 / 'CASOS99_FINAL.csv')
CASOS99_ORIGEN = pd.read_csv(dir_tabla_99 / 'CASOS99_ORIGEN.csv')

In [3]:
print(CASOS99_FINAL.shape)
print(CASOS99_ORIGEN.shape)

(194134, 13)
(198610, 13)


In [ ]:
## realizando antijoin
outer_join = CASOS99_FINAL.merge(CASOS99_ORIGEN, how = 'outer', indicator = True)
anti_join = outer_join[outer_join._merge == 'left_only'].drop('_merge', axis = 1)

anti_join = anti_join.drop_duplicates()  ## revisar algunos casos para ver porque inicialmente fueron detectados como doble marca
anti_join

In [4]:
CASOS99_ORIGEN['RBD_CARPETA'] = CASOS99_ORIGEN['rutaImagen1'].apply(lambda x: x.split('\\')[1])

In [5]:
CASOS99_ORIGEN.head()

Unnamed: 0    rbd  dvRbd  codigoCurso    serie             rutaImagen1  \
0       66780   5578      6         5197  4142763  CE\05197\4142763_1.jpg   
1       66783  11498      7         5012  4139762  CE\05012\4139762_1.jpg   
2       66795  20010      7         5015  4139795  CE\05015\4139795_1.jpg   
3       66902   5622      7         4943  4139026  CE\04943\4139026_1.jpg   
4       66912  11509      6         5078  4140736  CE\05078\4140736_1.jpg   

              rutaImagen2             rutaImagen3             rutaImagen4  \
0  CE\05197\4142763_2.jpg  CE\05197\4142763_3.jpg  CE\05197\4142763_4.jpg   
1  CE\05012\4139762_2.jpg  CE\05012\4139762_3.jpg  CE\05012\4139762_4.jpg   
2  CE\05015\4139795_2.jpg  CE\05015\4139795_3.jpg  CE\05015\4139795_4.jpg   
3  CE\04943\4139026_2.jpg  CE\04943\4139026_3.jpg  CE\04943\4139026_4.jpg   
4  CE\05078\4140736_2.jpg  CE\05078\4140736_3.jpg  CE\05078\4140736_4.jpg   

              rutaImagen5             rutaImagen6 preguntas  respuestas  \
0  CE\05197\4142763_5.jpg  CE\05197\4142763_6.jpg      p2_1          99   
1  CE\05012\4139762_5.jpg  CE\05012\4139762_6.jpg      p2_1          99   
2  CE\05015\4139795_5.jpg  CE\05015\4139795_6.jpg      p2_1          99   
3  CE\04943\4139026_5.jpg  CE\04943\4139026_6.jpg      p2_1          99   
4  CE\05078\4140736_5.jpg  CE\05078\4140736_6.jpg      p2_1          99   

  RBD_CARPETA  
0       05197  
1       05012  
2       05015  
3       04943  
4       05078

In [26]:
for preg in range(CASOS99_ORIGEN.shape[0]):
    pregunta_rev = CASOS99_ORIGEN.iloc[preg]
    
    rbd = pregunta_rev['RBD_CARPETA']
    estudiante = str(pregunta_rev['serie'])
    
    print('############################')
    print('RBD: ' + rbd)
    print('serie estudiante: ' + estudiante)
    print('preguntas: ' + pregunta_rev['preguntas'])
    print('############################')
    
    path_img = 'data\input_2\cuestionario_estudiantes'+ '\\' +rbd 
    path_img = Path(path_img)
    
    # páginas del cuardenillo
    pages = (n_pages, 1)
    # pregunta inicial páginas bajas
    q1 = 0
    # pregunta inicial páginas altas
    q2 = n_preguntas + 1
    
    for num_pag, pag in enumerate(path_img.glob(f'{estudiante}*')):
        
        folder, file = (pag.parts[-2], pag.parts[-1])
        print('#####')
        print('file:', file)
        print(f'num_pag: {num_pag}')
        
        file_no_ext = Path(file).with_suffix('')
        
        print(file_no_ext)
        # Creamos directorio si no existe
        Path(f'data/output_preg_99').mkdir(exist_ok=True)
        
        # Obtenemos página del archivo
        page = re.search('\d+$',str(file_no_ext)).group(0)
        
        
        # Leemos imagen
        img_preg = cv2.imread(str(pag),1)
        
        # Recortamos info innecesaria de imagen
        img_crop = recorte_imagen(img_preg, 0, 200, 50, 160)

        # Buscamos punto medio de imagen para dividirla en las dos páginas del cuadernillo
        punto_medio = int(np.round(img_crop.shape[1] / 2, 1))
        
        img_p1 = img_crop[:, :punto_medio] # página izquierda
        img_p2 = img_crop[:, punto_medio:] # página derecha
        
        # Obtenemos páginas del cuadernillo actual:
        if (num_pag % 2 == 0) & (num_pag != 0): # si n es par y no es la primera página
            pages = (pages[1]-1, pages[0] + 1) 
        elif num_pag % 2 == 1:
            pages = (pages[1]+1, pages[0] - 1)
        print(pages)
        
        
        # Para cada una de las dos imágenes del cuadernillo
        for p, media_img in enumerate([img_p1, img_p2]):
            
            print('####################')
            # Detecto recuadros naranjos
            m = get_mask_naranjo(media_img)
            
            # Obtengo contornos
            contours =cv2.findContours(m,cv2.RETR_EXTERNAL,cv2.CHAIN_APPROX_NONE)[0]
            # Me quedo contornos grandes
            big_contours = [i for i in contours if cv2.contourArea(i) > 30000]
            
            if pages[p] < pages[1-p]:
                # revertimos orden de contornos cuando es la página baja del cuadernillo
                big_contours = big_contours[::-1]
        
            for c in (big_contours):
                # Obtengo coordenadas de contornos
                x,y,w,h= cv2.boundingRect(c)
                img_pregunta = media_img[y:y+h, x:x+w]
                
                # Obtengo n° de pregunta en base a lógica de cuadernillo:
                if pages[p] > pages[1-p]: # si es la pág más alta del cuadernillo
                    q2 -= 1
                    q = q2
                elif (pages[p] < pages[1-p]) & (pages[p] != 1): # si es la pág más baja del cuardenillo
                    q1 += 1
                    q = q1
                else: # Para la portada
                    q = '_'
            
            # exportamos preguntas válidas:
                if 'p'+str(q) not in pregunta_rev['preguntas']:
                        pass
                else:
                            
                    try:
                        print('SUBPREGUNTAS')
                        # Obtenemos subpreguntas:
                        img_pregunta_crop = proc.recorte_imagen(img_pregunta)
                        img_crop_col = get_mask_naranjo(img_pregunta_crop, lower_color=np.array([0, 114, 139]), upper_color = np.array([17, 255, 255]))
                        #img_crop_col = proc.procesamiento_color(img_pregunta_crop)

                        puntoy = proc.obtener_puntos(img_crop_col)
                        
                        try:
                            for i in range(len(puntoy)-1):
                                print(i)
                                cropped_img_sub = img_pregunta_crop[puntoy[i]:puntoy[i+1],]
                                
                                aux = 'p'+ str(q)+ '_'+ str(i+1)
                                
                                if  aux == pregunta_rev['preguntas']:
                                    print('GUARDADO PREGUNTA')
                                    file_out = f'data/output_preg_99/{estudiante}_p{q}_{i+1}.jpg'
                                    print(file_out)
                                    cv2.imwrite(file_out, cropped_img_sub)
                                    print('PREGUNTA GUARDADA')
                                    
                        except Exception as e:
                            print('Ups, ocurrió un error al recortar la imagen con subpregunta ' + str(i+1))
                            print(e)
                            revisar_pregunta.append(q+ '__'+ str(i+1))
                    except Exception as e:
                    
                        print('Ups, ocurrió un error con la pregunta' + q)
                        print(e)
                        revisar_pregunta.append(q)

############################
RBD: 05197
serie estudiante: 4142763
preguntas: p2_1
############################
#####
file: 4142763_1.jpg
num_pag: 0
4142763_1
(12, 1)
####################
####################
#####
file: 4142763_2.jpg
num_pag: 1
4142763_2
(2, 11)
####################
SUBPREGUNTAS
[38, 39, 40, 41, 108, 109, 110, 111, 112, 156, 157, 158, 159, 203, 204, 205, 206, 250, 251, 252, 253, 254, 297, 298, 299, 300, 368, 369, 370, 371, 372, 416, 417, 418, 419, 487, 488, 489, 490, 533, 534, 535, 536, 537, 604, 605, 606, 607, 608, 675, 676, 677, 678, 679, 745]
[38, 39, 40, 41, 108, 109, 110, 111, 112, 156, 157, 158, 159, 203, 204, 205, 206, 250, 251, 252, 253, 254, 297, 298, 299, 300, 368, 369, 370, 371, 372, 416, 417, 418, 419, 487, 488, 489, 490, 533, 534, 535, 536, 537, 604, 605, 606, 607, 608, 675, 676, 677, 678, 679, 745]
[1, 2, 3, 5, 6, 7, 8, 10, 11, 12, 14, 15, 16, 18, 19, 20, 21, 23, 24, 25, 27, 28, 29, 30, 32, 33, 34, 36, 37, 38, 40, 41, 42, 43, 45, 46, 47, 48, 50, 51, 52, 5

TypeError: can only concatenate str (not "int") to str